# Using Gemma 3 (27B) to generate the stories and processing results
## Using the google SDK with Gemma 3 (27B) to generate the stories for the english and spanish related images
## Processing the results with both models, Gemma 3 (27B) and Gemini 2.0 Flash
## Obtaining final automated metrics and plots

In [ ]:
from google.colab import drive
import json
import os

# Mount Google Drive
drive.mount('/content/drive')

Mounted at /content/drive


In [ ]:
import json

# Load english dataset
with open("/content/drive/MyDrive/Project VIST with LLM/dataset_english.json", "r", encoding="utf-8") as f:
    stories = json.load(f)

# Filter stories with 5 or fewer images
filtered_en_stories = [story for story in stories if len(story.get("story", [])) <= 5]

# Save to a new file
with open("/content/drive/MyDrive/Project VIST with LLM/filtered_dataset_english.json", "w", encoding="utf-8") as f:
    json.dump(filtered_en_stories, f, indent=2, ensure_ascii=False)

In [ ]:
len(filtered_en_stories)

479

In [ ]:
import json

# Load spanish dataset
with open("/content/drive/MyDrive/Project VIST with LLM/dataset_spanish.json", "r", encoding="utf-8") as f:
    stories = json.load(f)

# Filter stories with 5 or fewer images
filtered_spa_stories = [story for story in stories if len(story.get("story", [])) <= 5]

# Save to a new file
with open("/content/drive/MyDrive/Project VIST with LLM/filtered_dataset_spanish.json", "w", encoding="utf-8") as f:
    json.dump(filtered_spa_stories, f, indent=2, ensure_ascii=False)

In [ ]:
len(filtered_spa_stories)

128

In [ ]:
# Matching images to the stories in english
import json, random
from pathlib import Path
from PIL import Image

# paths
BASE      = Path("/content/drive/MyDrive/Project VIST with LLM")
JSON_FILE = BASE / "filtered_dataset_english.json"
IMG_ROOT  = BASE / "english_img_albums"          # each sub-folder = one album

# load json
with open(JSON_FILE, encoding="utf-8") as f:
    albums = json.load(f)        # list[...]  all English albums

# helper
def find_album_folder(aid: str) -> Path | None:
    """Return the folder whose name ends with the album_id."""
    matches = list(IMG_ROOT.glob(f"*_{aid}"))
    return matches[0] if matches else None

# build pairs
paired_stories_eng = []

for album in albums:
    aid    = album["album_id"]
    folder = find_album_folder(aid)
    if not folder:
        print(f"[SKIP] no folder for {aid}")
        continue

    # texts (ordered by story_index)
    pages_sorted = sorted(album["story"], key=lambda p: p["story_index"])
    texts        = [p["text"] for p in pages_sorted]

    # images (00.jpg, 01.jpg, … sorted by filename)
    images = []
    for img_path in sorted(folder.iterdir()):
        if img_path.suffix.lower() in {".jpg", ".jpeg", ".png"}:
            try:
                #images.append(Image.open(img_path).convert("RGB"))
                images.append(img_path)
            except Exception as e:
                print(f"[WARN] {img_path.name}: {e}")

    paired_stories_eng.append(
        {"album_id": aid, "texts": texts, "images": images}
    )

print(f"Collected {len(paired_stories_eng)} story–image pairs")


Collected 479 story–image pairs


In [ ]:
from pathlib import Path

def normalize_paths(story_list: list) -> list:
    """Convert PosixPath entries to strings in the 'images' field of each dict."""
    normalized = []
    for story in story_list:
        story_copy = story.copy()
        story_copy['images'] = [str(p) if isinstance(p, Path) else p for p in story.get('images', [])]
        normalized.append(story_copy)
    return normalized

In [ ]:
norm_stories_eng=normalize_paths(paired_stories_eng)

In [ ]:
# Save to a new file
with open("/content/drive/MyDrive/Project VIST with LLM/filtered_dataset_with_imgs_path_english.json", "w", encoding="utf-8") as f:
    json.dump(norm_stories_eng, f, indent=2, ensure_ascii=False)

In [ ]:
norm_stories_eng

[{'album_id': 'f95e07f0-a0a0-4cd2-8db2-fa9823f68b30',
  'texts': ['"Father, Father!"\xa0I called. "Where are you?"\xa0 There was no answer. I sat helpless, wondering where he had gone.\n\nThen sticks and leaves crackled. I imagined a dark figure coming towards me.',
   'Maybe it was the old man with false teeth who grinned as he ate people!\n\n"Go away! Go away!" I cried.\nThen I heard a dog barking. It was getting closer and closer.',
   '"Help, Help! Someone help me!" I yelled. The crackling of leaves was getting closer and closer. Then, jumping and licking me, was Haffen, my pet dog.\n"Haffen! Haffen! You’ve found me," I cried.\n"Woof! Woof!" Haffen barked. He ran ahead of me. I couldn\'t see, only feel with my hands. I bumped into a tree root and fell over. I stepped into a thorn bush and cried as it pricked me. The darkness seemed endless. Haffen ran back and forth barking to keep me walking. But I could not move any further. I felt as if I had been swallowed up by the darkness.',

In [ ]:
# Matching images to the stories in english
import json, random
from pathlib import Path
from PIL import Image

# paths
BASE      = Path("/content/drive/MyDrive/Project VIST with LLM")
JSON_FILE = BASE / "filtered_dataset_spanish.json"
IMG_ROOT  = BASE / "spanish_img_albums"          # each sub-folder = one album

# load json
with open(JSON_FILE, encoding="utf-8") as f:
    albums = json.load(f)        # list[...]  all English albums

#selected = albums[:100]

# helper
def find_album_folder(aid: str) -> Path | None:
    """Return the folder whose name ends with the album_id."""
    matches = list(IMG_ROOT.glob(f"*_{aid}"))
    return matches[0] if matches else None

# build pairs
paired_stories_spa = []

for album in albums:
    aid    = album["album_id"]
    folder = find_album_folder(aid)
    if not folder:
        print(f"[SKIP] no folder for {aid}")
        continue

    # texts (ordered by story_index)
    pages_sorted = sorted(album["story"], key=lambda p: p["story_index"])
    texts        = [p["text"] for p in pages_sorted]

    # images (00.jpg, 01.jpg, … sorted by filename)
    images = []
    for img_path in sorted(folder.iterdir()):
        if img_path.suffix.lower() in {".jpg", ".jpeg", ".png"}:
            try:
                #images.append(Image.open(img_path).convert("RGB"))
                images.append(img_path)
            except Exception as e:
                print(f"[WARN] {img_path.name}: {e}")

    paired_stories_spa.append(
        {"album_id": aid, "texts": texts, "images": images}
    )

print(f"Collected {len(paired_stories_spa)} story–image pairs")


Collected 128 story–image pairs


In [ ]:
norm_stories_spa=normalize_paths(paired_stories_spa)

In [ ]:
norm_stories_spa

[{'album_id': 'dd4c4d9e-9f6a-45ba-9867-cdbe7b9774e2',
  'texts': ['Ya pasaron varios meses. He crecido mucho últimamente. Creo que ya no quepo aquí en donde me encuentro.\xa0 Mi mami ya sabe cuando naceré. Creo que será ¡hoy! es ¡hoy!, es ¡hoy!Por fin conoceré a mamá y a papá. ¿Cómo serán? ¿Me querrán como yo los quiero?¿Será que ellos van a jugar conmigo? Tengo tantas preguntas. Ya estoy feliz pensando en estar con ellos siempre.',
   'Mi papá estaba angustiado en la sala de espera. No le daban noticias de mi nacimiento. El médico llega y le cuenta que soy un hermoso bebé.\nLe pide que se coloque una bata para entrar a conocerme. Al verme, papá llora de felicidad.\nYo sé que mi mamá es una guerrera. Ella siempre luchará por mí.\xa0 Me va a proteger toda la vida. Me va a alimentar y resguardar de todo peligro. Ya quiero estar en casa y conocer todo lo que me tienen preparado.',
   'Las mamás son muy dulces. Siempre saben qué es lo mejor para ti. Cuando estás en un problema, siempre te 

In [ ]:
# Save to a new file
with open("/content/drive/MyDrive/Project VIST with LLM/filtered_dataset_with_imgs_path_spanish.json", "w", encoding="utf-8") as f:
    json.dump(norm_stories_spa, f, indent=2, ensure_ascii=False)

In [ ]:
!pip install json5

In [ ]:
from PIL import Image
import os
import json5
import time
from google import genai
from google.genai import types
import typing_extensions as typing
from google.colab import userdata


# Schema for the visual storytelling task structured generation
# The Gemini/Gemma model output format will follow this
class StoryPart(typing.TypedDict):
    image: typing.Annotated[int, "Should be the number in order according to the number of images in the input."]
    story_part: typing.Annotated[str, "Should be the generated story for the corresponding image in order."]

class Story(typing.TypedDict):
    story: list[StoryPart]
##########################################

#Images for one-shot examples in english
image_eng_path1 = "/content/drive/MyDrive/Project VIST with LLM/one_shot_examples/english/00.png"
image_eng_path2 = "/content/drive/MyDrive/Project VIST with LLM/one_shot_examples/english/01.png"
image_eng_path3 = "/content/drive/MyDrive/Project VIST with LLM/one_shot_examples/english/02.png"
image_eng_path4 = "/content/drive/MyDrive/Project VIST with LLM/one_shot_examples/english/03.png"
image_eng_path5 = "/content/drive/MyDrive/Project VIST with LLM/one_shot_examples/english/04.png"

image_eng1 = Image.open(image_eng_path1)
image_eng2 = Image.open(image_eng_path2)
image_eng3 = Image.open(image_eng_path3)
image_eng4 = Image.open(image_eng_path4)
image_eng5 = Image.open(image_eng_path5)

#Images for one-shot examples in spanish
image_spa_path1 = "/content/drive/MyDrive/Project VIST with LLM/one_shot_examples/spanish/00.jpg"
image_spa_path2 = "/content/drive/MyDrive/Project VIST with LLM/one_shot_examples/spanish/01.png"
image_spa_path3 = "/content/drive/MyDrive/Project VIST with LLM/one_shot_examples/spanish/02.jpg"
image_spa_path4 = "/content/drive/MyDrive/Project VIST with LLM/one_shot_examples/spanish/03.png"
image_spa_path5 = "/content/drive/MyDrive/Project VIST with LLM/one_shot_examples/spanish/04.jpg"

image_spa1 = Image.open(image_spa_path1)
image_spa2 = Image.open(image_spa_path2)
image_spa3 = Image.open(image_spa_path3)
image_spa4 = Image.open(image_spa_path4)
image_spa5 = Image.open(image_spa_path5)

class GenAIAgent:
    """
    A utility class for interacting with Google's GenAI models,
    handling synchronous generation.
    """

    # Configuration constants
    DEFAULT_FLASH_MODEL_ID = "gemini-2.0-flash"
    DEFAULT_CONCURRENT_INPUT_TOKENS_LIMIT = 8192
    #System Prompt for the model
    ENGLISH_SYSTEM_PROMPT = \
    '''
    You are an expert storyteller. You are not overly verbose in your stories, and you keep them very interesting.
    Your stories need to be in third person, from an external point of view.
    Craft an engaging story based strictly on the following figures presented in order.
    Follow the schema as defined for your output:
    {{
    "story": [
        {
        "image": <int>,
        "story_part": "<str>"
        },
        ...
    ]
    }}
    '''
    SPANISH_SYSTEM_PROMPT = \
    '''
    Eres un narrador experto en español. No eres excesivamente verboso en tus historias y las mantienes muy interesantes.
    Tus historias necesitan ser creadas en tercera persona, desde un punto de vista externo.
    Crea una historia atractiva basada estrictamente en las siguientes imágenes presentadas en orden.
    Sigue el esquema definido para tu respuesta:
    {{
    "story": [
        {
        "image": <int>,
        "story_part": "<str>"
        },
        ...
    ]
    }}
    '''

    # Standard safety configurations
    API_SAFETY_SETTINGS = [
        types.SafetySetting(category="HARM_CATEGORY_HATE_SPEECH", threshold="OFF"),
        types.SafetySetting(category="HARM_CATEGORY_DANGEROUS_CONTENT", threshold="OFF"),
        types.SafetySetting(category="HARM_CATEGORY_SEXUALLY_EXPLICIT", threshold="OFF"),
        types.SafetySetting(category="HARM_CATEGORY_HARASSMENT", threshold="OFF")
    ]

    #User prompt used for the model with each english language task
    LLM_VIST_GEN_USER_ENGLISH_PROMPT = \
    f'''
    You are an expert storyteller. You are not overly verbose in your stories, and you keep them very interesting.
    Your stories need to be in third person, from an external point of view.
    Craft an engaging story based strictly on the following figures presented in order.
    Follow the schema as defined for your output:
    {{
    "story": [
        {{
        "image": <int>,
        "story_part": "<str>"
        }},
        ...
    ]
    }}

    First I will show you an example of how to do it:
    INPUT:
    Image 1:
    {image_eng1}
    Image 2:
    {image_eng2}
    Image 3:
    {image_eng3}
    Image 4:
    {image_eng4}
    Image 5:
    {image_eng5}
    OUTPUT:
    {{
    "story": [
        {{
        "image": 1,
        "story_part": "I am big. I am bigger than a stream. I have lot of water. My water is used for drinking. They say I always run. I never walk. My water moves from here to there. They say I flow."
        }},
        {{
        "image": 2,
        "story_part": "I have a mouth. But I never eat. I can't even talk. You hear the sound when I flow. I move soil and small rocks. I help move logs of wood. I do so much work but I don't have hands."
        }},
        {{
        "image": 3,
        "story_part": "I have a bed. But I don't sleep. I am always awake. I am always moving. I make soil. I make valleys. My water is sweet."
        }},
        {{
        "image": 4,
        "story_part": "Let me tell you again. I have no legs but I can run. I can't eat or talk but I have a mouth. I have a long bed but I never sleep. I have a bank but there is no money in it. Did you guess who am I?"
        }},
        {{
        "image": 5,
        "story_part": "A river! I am a river. Do you know some names I have?"
        }}
    ]
    }}

    Now generate the story for the user's input.

    ----INPUT STARTS HERE----
    '''

    #User prompt used for the model with each english language task
    LLM_VIST_GEN_USER_SPANISH_PROMPT = \
    f'''
    Eres un narrador experto en español. No eres excesivamente verboso en tus historias y las mantienes muy interesantes.
    Tus historias necesitan ser creadas en tercera persona, desde un punto de vista externo.
    Crea una historia atractiva basada estrictamente en las siguientes imágenes presentadas en orden.
    Sigue el esquema definido para tu respuesta:
    {{
    "story": [
        {{
        "image": <int>,
        "story_part": "<str>"
        }},
        ...
    ]
    }}
    Primero te enseñaré un ejemplo sobre como hacerlo:
    INPUT:
    Imagen 1:
    {image_spa1}
    Imagen 2:
    {image_spa2}
    Imagen 3:
    {image_spa3}
    Imagen 4:
    {image_spa4}
    Imagen 5:
    {image_spa5}
    OUTPUT:
    {{
    "story": [
        {{
        "image": 1,
        "story_part": "Ya pasaron varios meses. He crecido mucho últimamente. Creo que ya no quepo aquí en donde me encuentro.  Mi mami ya sabe cuando naceré. Creo que será ¡hoy! es ¡hoy!, es ¡hoy!Por fin conoceré a mamá y a papá. ¿Cómo serán? ¿Me querrán como yo los quiero?¿Será que ellos van a jugar conmigo? Tengo tantas preguntas. Ya estoy feliz pensando en estar con ellos siempre."
        }},
        {{
        "image": 2,
        "story_part": "Mi papá estaba angustiado en la sala de espera. No le daban noticias de mi nacimiento. El médico llega y le cuenta que soy un hermoso bebé.\nLe pide que se coloque una bata para entrar a conocerme. Al verme, papá llora de felicidad.\nYo sé que mi mamá es una guerrera. Ella siempre luchará por mí.  Me va a proteger toda la vida. Me va a alimentar y resguardar de todo peligro. Ya quiero estar en casa y conocer todo lo que me tienen preparado."
        }},
        {{
        "image": 3,
        "story_part": "Las mamás son muy dulces. Siempre saben qué es lo mejor para ti. Cuando estás en un problema, siempre te acompañan. Mamá siempre se preocupa cuando estás lejos. Le pide a Dios que te proteja.\n\n Papá siempre está con ella apoyándola. Juntos quieren verte crecer y que te conviertas en una persona de bien. Quieren que estudies y tengas un buen futuro."
        }},
        {{
        "image": 4,
        "story_part": "Papá y mamá son personas increíbles. Son como ángeles que nos cuidan sin importar la edad que tengamos. Si somos bebés, niños, adolescentes o personas adultas, siempre están para apoyarnos.\nCuando pase el tiempo y ellos envejezcan, debo cuidar de ellos, así como ellos cuidaron de mí.  Me enseñaron a caminar, a amarrarme las agujetas de los zapatos, a aprender, a ser feliz y a vivir en paz.\nMis papás son lo mejor que he tenido.  Siempre los llevo y llevaré en mi corazón. ¡Somos una hermosa familia!"
        }},
        {{
        "image": 5,
        "story_part": "¡Mi familia!"
        }}
    ]
    }}

    Ahora genera la historia para el input del usuario.
    IMPORTANTE: El output debe estar en idioma español.

    ----EL INPUT EMPIEZA AQUí----
    '''

    def __init__(
        self,
        specified_model_id: str = None,
        select_system_prompt: str = None,
    ):
        """
        Initializes the GenAIAgent with model and system prompt settings.

        Args:
            specified_model_id (str, optional): The ID of the model to use.
                                              Defaults to DEFAULT_FLASH_MODEL_ID.
            custom_system_prompt (str, optional): A custom system instruction.
                                                Defaults to DEFAULT_SYSTEM_PROMPT.
            api_key (str, optional): Your Google API key. If None, it will attempt
                                     to use the key passed during client initialization
                                     (e.g., via genai.configure or environment variable).
        """
        self.chosen_model_id = specified_model_id or self.DEFAULT_FLASH_MODEL_ID
        if select_system_prompt:
            if select_system_prompt == "Spanish":
                self.active_system_prompt = self.SPANISH_SYSTEM_PROMPT
                self.active_user_prompt = self.LLM_VIST_GEN_USER_SPANISH_PROMPT
            else:
                self.active_system_prompt = self.ENGLISH_SYSTEM_PROMPT
                self.active_user_prompt = self.LLM_VIST_GEN_USER_ENGLISH_PROMPT
        else:
            self.active_system_prompt = self.ENGLISH_SYSTEM_PROMPT
            self.active_user_prompt = self.LLM_VIST_GEN_USER_ENGLISH_PROMPT


        api_key = userdata.get("GOOGLE_API_KEY")

        self.genai_client = genai.Client(api_key=api_key) # Client for generation

        self.output_token_cap = 8192 # Maximum tokens for model response

    def generate_single_response(
        self,
        input_content_list: list,
        response_schema_definition,
        include_metrics_log: bool = False
    ):
        """
        Generates a single content response from the model.
        """
        request_start_time = time.time()
        if(self.chosen_model_id=="gemini-2.0-flash"):
            content_generation_config = types.GenerateContentConfig(
                temperature=1,
                system_instruction=self.active_system_prompt,
                max_output_tokens=self.output_token_cap,
                response_modalities=["TEXT"],
                response_mime_type = "application/json",
                response_schema = response_schema_definition,
                safety_settings=self.API_SAFETY_SETTINGS
            )
        #Gemma 3 with the API does not support structured output or System Prompt
        else:
            content_generation_config = types.GenerateContentConfig(
                temperature=1,
                max_output_tokens=self.output_token_cap,
                response_modalities=["TEXT"],
                safety_settings=self.API_SAFETY_SETTINGS
            )

        api_response = self.genai_client.models.generate_content(
            model=self.chosen_model_id,
            contents=input_content_list,
            config=content_generation_config,
        )

        generated_text = api_response.text
        if include_metrics_log:
            performance_log = {
                "model_used": self.chosen_model_id,
                "output_tokens": api_response.usage_metadata.candidates_token_count,
                "input_tokens": api_response.usage_metadata.prompt_token_count,
                "elapsed_time_sec": round(time.time() - request_start_time, 2),
            }
            return generated_text, performance_log
        return generated_text

In [ ]:
# LLM Logic
def generate_story_with_llm(image_data_list, llm_model_name, language):
    """
    Function to generate a story using an LLM.
    Returns a list of story segments, one for each image.

    Args:
        image_data_list (list): A list of image data (e.g., bytes).
        llm_model_name (str): The name of the selected LLM.
        language (str): The selected language ("English" or "Spanish").

    Returns:
        list[str]: A list of story segments, or an empty list/error indication.
    """
    num_images = len(image_data_list)
    story_segments = []
    model_name = ""
    if llm_model_name == "Gemma 3 (27B)":
        model_name = "gemma-3-27b-it"
    else:
        model_name = "gemini-2.0-flash"

    # Instance of the agent for story generation
    ai_handler = GenAIAgent(specified_model_id=model_name, select_system_prompt=language)
    # Story generation logic
    if num_images > 0:
        user_content = [ai_handler.active_user_prompt]
        for i, image in enumerate(image_data_list):
            if language == "Spanish":
                user_content.append(f"Imagen {i+1}:")
            else:
                user_content.append(f"Image {i+1}:")
            user_content.append(image)

    schema = Story
    gen_story, log = ai_handler.generate_single_response(input_content_list=user_content, response_schema_definition=schema, include_metrics_log = True)
    if gen_story == None:
        return None, None
    text = gen_story.replace("```json","")
    text = text.replace("```","")
    print(gen_story)
    final_story = json5.loads(text)
    print(final_story)
    print("Generation successful!")
    print(log)
    for part in final_story["story"]:
        story_segments.append(part["story_part"])
    return story_segments, log

In [ ]:
len(norm_stories_eng)

479

In [ ]:
norm_stories_eng

[{'album_id': 'f95e07f0-a0a0-4cd2-8db2-fa9823f68b30',
  'texts': ['"Father, Father!"\xa0I called. "Where are you?"\xa0 There was no answer. I sat helpless, wondering where he had gone.\n\nThen sticks and leaves crackled. I imagined a dark figure coming towards me.',
   'Maybe it was the old man with false teeth who grinned as he ate people!\n\n"Go away! Go away!" I cried.\nThen I heard a dog barking. It was getting closer and closer.',
   '"Help, Help! Someone help me!" I yelled. The crackling of leaves was getting closer and closer. Then, jumping and licking me, was Haffen, my pet dog.\n"Haffen! Haffen! You’ve found me," I cried.\n"Woof! Woof!" Haffen barked. He ran ahead of me. I couldn\'t see, only feel with my hands. I bumped into a tree root and fell over. I stepped into a thorn bush and cried as it pricked me. The darkness seemed endless. Haffen ran back and forth barking to keep me walking. But I could not move any further. I felt as if I had been swallowed up by the darkness.',

In [ ]:
from PIL import Image
from tqdm import tqdm
import time
from pathlib import Path

llm_model_name = "Gemma 3 (27B)" # "Gemini 2.0 Flash"
language = "English"
path_results = "/content/drive/MyDrive/Project VIST with LLM/results/results_gemma3_eng.json"
json_path_results = Path(path_results)
path_logs = "/content/drive/MyDrive/Project VIST with LLM/results/logs_gemma3_eng.json"
json_path_logs = Path(path_logs)

results = {}
logs = []
log_bundle = {}
count = 1
start_time = time.time()

for story_eng in tqdm(norm_stories_eng):
  if json_path_results.exists():
    with open(json_path_results, "r", encoding="utf-8") as f:
        results_processed = json.load(f)
  else:
    results_processed = []
  if json_path_logs.exists():
    with open(json_path_logs, "r", encoding="utf-8") as f:
        logs = json.load(f)
  else:
    logs = []

  already_processed = [entry["album_id"] for entry in results_processed]
  current_album_id  = story_eng.get("album_id")
  if current_album_id in already_processed:
    continue
  print(already_processed)

  images_list = story_eng.get("images")
  images_for_llm = []
  for image_path in images_list:
    images_for_llm.append(Image.open(image_path))

  gen_story, log = generate_story_with_llm(images_for_llm, llm_model_name, language)
  if((count%30) == 0): #there is an API limit of only 30 API calls per minute for gemma 3, so gotta validate we are not violating that
      time_taken = time.time() - start_time
      while (time_taken < 60):
          time.sleep(61-time_taken)
          time_taken = time.time() - start_time
      start_time = time.time()
  if gen_story == None:
    continue
  if(len(story_eng.get("texts")) == len(gen_story)):
    results["album_id"] = story_eng.get("album_id")
    results["texts"] = story_eng.get("texts")
    results["images"] = story_eng.get("images")
    results["predicted_texts"] = gen_story
    results_processed.append(results) #appending all the fields of final results for each story

    log_bundle[f"album_id"] = story_eng.get("album_id")
    log_bundle[f"log"] = log #saving the logs
    logs.append(log_bundle)

    # Saving all to not lose progress by an external error
    # Save results to a JSON file
    with open(json_path_results, "w", encoding="utf-8") as f:
        json.dump(results_processed, f, indent=2, ensure_ascii=False)

    # Save logs (a list of log_bundle dicts) to a separate JSON file
    with open(json_path_logs, "w", encoding="utf-8") as f:
        json.dump(logs, f, indent=2, ensure_ascii=False)
    print("Files Successfully saved!")

  count+=1

  3%|▎         | 14/479 [00:00<00:03, 137.30it/s]

['f95e07f0-a0a0-4cd2-8db2-fa9823f68b30', '76dd0f6d-b076-41d3-8cf8-94fc4abb010f', 'c7aa10d4-5a18-46ff-8b41-0fb2fccdd6d3', '9e97ce04-6231-40ed-b560-eff01f77c243', 'dc0f9730-a61a-4a9a-a4d2-bcab63f76de0', 'db3cba94-4f01-4174-8c66-24c6d801c1d5', '1b7941f7-7a03-455c-9d28-fa812478b21b', 'fcc76475-40a3-4fa9-9116-b856af6b25a4', '55eb5e21-b65b-463a-a067-613ad93411cc', '16ef129a-9940-4940-abd6-b600a67888b5', 'b6a9ee36-af16-4f9e-93e1-fbb1a38f1a65', '6a656440-ce72-4acb-9dcb-995e7674155a', '13cc99f0-3ed5-404f-866c-a1e8c86e87d3', '6f4fc57c-2807-443f-952f-23dac9c8f382', 'cea3a365-7f96-4bb3-97c1-07fd0ecef3ca', '2c727efc-865e-450f-97c0-68797385a195', '002fbc8b-8158-4fbc-9963-3d3ea8e5eee1', '1c3aa054-579c-4c66-b2eb-eeecc3650d2b', '7ccbec4e-5faa-4f3e-9f66-5f36c822ae92', '22ed543e-2f22-47ce-ba0e-ef556ac11483', '4b91e5b0-5941-4455-89cf-8067386e8c10', '847a3b56-312d-4713-9018-ddbd168813b9', 'b6111e95-c74e-4c35-8c4d-c8b08e4b12ca', 'fd621d02-7d09-4763-b195-e1aed4e8bf25', '432652a8-3250-40f0-8320-337a3ecc7194',

  6%|▌         | 28/479 [00:06<02:09,  3.48it/s] 

```json
{
    "story": [
        {
        "image": 1,
        "story_part": "It began as a tight bud, hidden amongst green. A secret held close, waiting for warmth. The world rushed by, unaware of the potential within."
        },
        {
        "image": 2,
        "story_part": "Slowly, the petals unfurled, a gentle stretch towards the sun. Each layer revealed a soft, grey hue, a quiet elegance against the vibrant backdrop."
        },
        {
        "image": 3,
        "story_part": "The center, a pale circle, offered a promise of sweetness. Bees buzzed closer, drawn by an unseen invitation. It stood alone, a simple beauty."
        },
        {
        "image": 4,
        "story_part": "A single breeze threatened to tear it from its stem, but it held firm. Resilience wasn't in its grand display, but in its quiet persistence."
        },
        {
        "image": 5,
        "story_part": "It bloomed not for admiration, but simply because it was time. A fleeting moment of grac

 10%|█         | 48/479 [00:15<02:11,  3.27it/s]

...

```json
{
    "story": [
        {
            "image": 1,
            "story_part": "The teacher pointed to the smoke rising in the distance. A worried murmur went through the classroom. It wasn't rain, and it wasn't from a cooking fire. Something was burning."
        },
        {
            "image": 2,
            "story_part": "After school, the teacher led a small group to investigate. They found a clearing and built a small fire of their own, a familiar comfort against the growing unease. They needed a plan."
        },
        {
            "image": 3,
            "story_part": "While they discussed, someone remembered the corn. Roasted over the embers, it offered a small distraction, a moment of normalcy before facing whatever lay beyond the smoke."
        }
    ]
}
```
{'story': [{'image': 1, 'story_part': "The teacher pointed to the smoke rising in the distance. A worried murmur went through the classroom. It wasn't rain, and it wasn't from a cooking fire. Something was bur

100%|█████████▉| 478/479 [1:10:03<00:07,  7.99s/it]

```json
{
    "story": [
        {
            "image": 1,
            "story_part": "Old Man Tiberi was known for his stories, but also for his stubbornness. He refused help, even when his bones ached with the damp. The young man, Kito, offered a hand, but Tiberi just waved his cane, a silent dismissal. The dog, Mlima, watched with knowing eyes."
        },
        {
            "image": 2,
            "story_part": "Kito didn't give up easily. He knew Tiberi’s stories held the village’s history. He proposed a challenge: a test of strength, a simple hand-pull. If Kito won, Tiberi would accept assistance. Tiberi, intrigued, agreed."
        }
    ]
}
```
{'story': [{'image': 1, 'story_part': 'Old Man Tiberi was known for his stories, but also for his stubbornness. He refused help, even when his bones ached with the damp. The young man, Kito, offered a hand, but Tiberi just waved his cane, a silent dismissal. The dog, Mlima, watched with knowing eyes.'}, {'image': 2, 'story_part': "Kito

100%|██████████| 479/479 [1:10:09<00:00,  8.79s/it]

```json
{
    "story": [
        {
            "image": 1,
            "story_part": "She drifted among the stars, a silent guardian with wings of light. Her purpose was unknown, even to herself, a gentle presence in the vast darkness."
        },
        {
            "image": 2,
            "story_part": "Below, a girl watched the sky, dreaming of journeys beyond the clouds. She imagined soaring with the birds, or riding on the silver wings of the distant plane."
        }
    ]
}
```
{'story': [{'image': 1, 'story_part': 'She drifted among the stars, a silent guardian with wings of light. Her purpose was unknown, even to herself, a gentle presence in the vast darkness.'}, {'image': 2, 'story_part': 'Below, a girl watched the sky, dreaming of journeys beyond the clouds. She imagined soaring with the birds, or riding on the silver wings of the distant plane.'}]}
Generation successful!
{'model_used': 'gemma-3-27b-it', 'output_tokens': None, 'input_tokens': 1259, 'elapsed_time_sec': 5.5

In [ ]:
from PIL import Image
from tqdm import tqdm
import time
from pathlib import Path

llm_model_name = "Gemma 3 (27B)" # "Gemini 2.0 Flash"
language = "Spanish"
path_results = "/content/drive/MyDrive/Project VIST with LLM/results/results_gemma3_spa.json"
json_path_results = Path(path_results)
path_logs = "/content/drive/MyDrive/Project VIST with LLM/results/logs_gemma3_spa.json"
json_path_logs = Path(path_logs)

results = {}
logs = []
log_bundle = {}
count = 1
start_time = time.time()

for story_spa in tqdm(norm_stories_spa):
  if json_path_results.exists():
    with open(json_path_results, "r", encoding="utf-8") as f:
        results_processed = json.load(f)
  else:
    results_processed = []
  if json_path_logs.exists():
    with open(json_path_logs, "r", encoding="utf-8") as f:
        logs = json.load(f)
  else:
    logs = []

  already_processed = [entry["album_id"] for entry in results_processed]
  current_album_id  = story_spa.get("album_id")
  if current_album_id in already_processed:
    continue
  print(already_processed)

  images_list = story_spa.get("images")
  images_for_llm = []
  for image_path in images_list:
    images_for_llm.append(Image.open(image_path))

  gen_story, log = generate_story_with_llm(images_for_llm, llm_model_name, language)

  if((count%30) == 0): #there is an API limit of only 30 API calls per minute for gemma 3, so gotta validate we are not violating that
      time_taken = time.time() - start_time
      while (time_taken < 60):
          time.sleep(61-time_taken)
          time_taken = time.time() - start_time
      start_time = time.time()
  if gen_story == None:
    continue
  if(len(story_spa.get("texts")) == len(gen_story)):
    results["album_id"] = story_spa.get("album_id")
    results["texts"] = story_spa.get("texts")
    results["images"] = story_spa.get("images")
    results["predicted_texts"] = gen_story
    results_processed.append(results) #appending all the fields of final results for each story

    log_bundle[f"album_id"] = story_spa.get("album_id")
    log_bundle[f"log"] = log #saving the logs
    logs.append(log_bundle)

    # Saving all to not lose progress by an external error
    # Save results to a JSON file
    with open(json_path_results, "w", encoding="utf-8") as f:
        json.dump(results_processed, f, indent=2, ensure_ascii=False)

    # Save logs (a list of log_bundle dicts) to a separate JSON file
    with open(json_path_logs, "w", encoding="utf-8") as f:
        json.dump(logs, f, indent=2, ensure_ascii=False)
    print("Files Successfully saved!")

  # if count == 3:
  #   break
  count+=1

  0%|          | 0/128 [00:00<?, ?it/s]

[]


  1%|          | 1/128 [00:11<24:01, 11.35s/it]

```json
{
    "story": [
        {
            "image": 1,
            "story_part": "La sala de espera era un hervidero de rostros ansiosos. Cada persona tenía su propia historia, su propia esperanza. Él esperaba su turno, un trámite burocrático que parecía eterno. La incertidumbre flotaba en el aire, mezclada con el cansancio de la espera."
        },
        {
            "image": 2,
            "story_part": "La alegría llegó con la llegada de un nuevo miembro a la familia. Un pequeño ser, lleno de vida, que unió aún más a la pareja. El amor se multiplicó, creando un hogar lleno de sonrisas y promesas."
        },
        {
            "image": 3,
            "story_part": "El instinto maternal es poderoso, un lazo irrompible que protege y nutre. Como la leona con su cachorro, la madre velaba por su pequeño, ofreciéndole seguridad y cariño incondicional."
        },
        {
            "image": 4,
            "story_part": "Un momento de pura conexión. La madre alza a su hijo, mo

  2%|▏         | 2/128 [00:16<16:43,  7.96s/it]

...

```json
{
    "story": [
        {
            "image": 1,
            "story_part": "El viento soplaba con fuerza en la ladera. Tres amigos jugaban despreocupadamente con una cometa colorida, sin notar las nubes grises que se acercaban. De repente, una ráfaga más fuerte de lo normal arrancó la cometa de sus manos, llevándola hacia un terraplén rocoso."
        },
        {
            "image": 2,
            "story_part": "El niño del sombrero amarillo corrió tras la cometa, decidido a recuperarla. Sus amigos lo siguieron, preocupados por su seguridad. El terreno era inestable y la caída, peligrosa. El niño, sin embargo, solo pensaba en su cometa."
        }
    ]
}
```
{'story': [{'image': 1, 'story_part': 'El viento soplaba con fuerza en la ladera. Tres amigos jugaban despreocupadamente con una cometa colorida, sin notar las nubes grises que se acercaban. De repente, una ráfaga más fuerte de lo normal arrancó la cometa de sus manos, llevándola hacia un terraplén rocoso.'}, {'image':

 99%|█████████▉| 127/128 [18:40<00:06,  6.39s/it]

```json
{
    "story": [
        {
            "image": 1,
            "story_part": "El pequeño lagarto, de escamas verde esmeralda, era el rey de su rama. Observaba el mundo con ojos dorados, atento a cualquier movimiento. Su reino era un laberinto de hojas y sol, y él, su silencioso guardián."
        },
        {
            "image": 2,
            "story_part": "Doña Elena, con sus manos llenas de tierra y su sonrisa sabia, cuidaba su jardín como si fuera un tesoro. Cada flor, cada planta, era un pedazo de su corazón. El jardín era un refugio, un lugar donde el tiempo parecía detenerse."
        }
    ]
}
```
{'story': [{'image': 1, 'story_part': 'El pequeño lagarto, de escamas verde esmeralda, era el rey de su rama. Observaba el mundo con ojos dorados, atento a cualquier movimiento. Su reino era un laberinto de hojas y sol, y él, su silencioso guardián.'}, {'image': 2, 'story_part': 'Doña Elena, con sus manos llenas de tierra y su sonrisa sabia, cuidaba su jardín como si fuera un

100%|██████████| 128/128 [18:53<00:00,  8.86s/it]

```json
{
    "story": [
        {
            "image": 1,
            "story_part": "El hombre levantó el rifle, apuntando con furia. El perro, asustado, aullaba y se retorcía, intentando escapar de su agarre. La violencia se cernía sobre el paisaje árido, un presagio de un acto cruel e innecesario."
        },
        {
            "image": 2,
            "story_part": "Dos mujeres, vestidas con ropas tradicionales, observaban la escena a la distancia. Sus rostros reflejaban preocupación y un silencioso reproche. Una de ellas apretaba un cesto contra su pecho, como si buscara consuelo en su contenido."
        },
        {
            "image": 3,
            "story_part": "El joven, ahora sin el rifle, acariciaba la cabeza del perro. La mujer mayor lo observaba con severidad, mientras que la otra, más joven, parecía ofrecerle una mirada de comprensión. El perro, aún tembloroso, buscaba refugio en el contacto humano."
        },
        {
            "image": 4,
            "story_par

## Plotting Results

In [ ]:
nltk.download('punkt')

[nltk_data] Downloading package punkt to /root/nltk_data...
[nltk_data]   Package punkt is already up-to-date!


True

In [ ]:
import json
import nltk
from nltk.translate.bleu_score import sentence_bleu, SmoothingFunction
from nltk.translate.meteor_score import meteor_score
from nltk.tokenize import word_tokenize
import numpy as np
import matplotlib.pyplot as plt
import os

#NLTK Resource Downloads
def download_nltk_resources():
    resources_to_download = {
        "punkt": 'tokenizers/punkt', # Includes general and some language-specific data
        "wordnet": 'corpora/wordnet',
        "omw-1.4": 'corpora/omw-1.4',
        "averaged_perceptron_tagger": 'taggers/averaged_perceptron_tagger'
    }

    for resource_name, resource_path in resources_to_download.items():
        try:
            nltk.data.find(resource_path)
            print(f"NLTK resource '{resource_name}' already available.")
        except LookupError:
            print(f"Downloading NLTK resource '{resource_name}'...")
            try:
                nltk.download(resource_name, quiet=True) # quiet download
                print(f"NLTK resource '{resource_name}' downloaded successfully.")
            except Exception as e:
                print(f"Error downloading NLTK resource '{resource_name}': {e}")


download_nltk_resources()

# Global Settings & Initializations
CHENCHERRY = SmoothingFunction()
PLOTS_DIR = "comparison_plots"
os.makedirs(PLOTS_DIR, exist_ok=True)

# Metric Calculation Function
def calculate_metrics_for_file(filepath, language_code='english'): # Added language_code
    """
    Loads a JSON file, calculates specified metrics for each item, and returns averages.
    'language_code' should be 'english' or 'spanish' for NLTK tokenization.
    """
    bleu_scores = []
    meteor_scores = []
    predicted_lengths = []
    reference_lengths = []

    try:
        with open(filepath, 'r', encoding='utf-8') as f:
            data = json.load(f)
    except FileNotFoundError:
        print(f"Error: File not found at {filepath}")
        return None

    if not isinstance(data, list):
        print(f"Error: Expected a list of items in {filepath}, but got {type(data)}")
        return None

    print(f"Processing {filepath} ({len(data)} items) for language: {language_code}...")
    for i, item in enumerate(data):

        if not isinstance(item, dict):
            print(f"Warning: Item {i} in {filepath} is not a dictionary. Skipping.")
            continue

        reference_segments = item.get("texts")
        predicted_segments = item.get("predicted_texts")

        if reference_segments is None or predicted_segments is None:
            print(f"Warning: Missing 'texts' or 'predicted_texts' in item {i} of {filepath}. Skipping.")
            continue
        if not isinstance(reference_segments, list) or not isinstance(predicted_segments, list):
            print(f"Warning: 'texts' or 'predicted_texts' is not a list in item {i} of {filepath}. Skipping.")
            continue

        reference_segments = [str(s) for s in reference_segments]
        predicted_segments = [str(s) for s in predicted_segments]

        full_reference_story = " ".join(reference_segments)
        full_predicted_story = " ".join(predicted_segments)

        try:
            # Try tokenizing with specified language
            ref_tokens = word_tokenize(full_reference_story.lower(), language=language_code)
            pred_tokens = word_tokenize(full_predicted_story.lower(), language=language_code)
        except LookupError as e_lookup:
            # This is where 'punkt_tab' or similar might be requested
            print(f"Warning: Language-specific tokenization failed for item {i} in {filepath} (lang: {language_code}). Error: {e_lookup}. Falling back to default tokenization.")
            try:
                # Fallback to default (often English-biased) tokenization
                ref_tokens = word_tokenize(full_reference_story.lower())
                pred_tokens = word_tokenize(full_predicted_story.lower())
            except Exception as e_fallback:
                print(f"Fatal: Default tokenization also failed for item {i}. Error: {e_fallback}. Skipping item.")
                continue # Skip this item entirely
        except Exception as e_general:
            print(f"Warning: General tokenization error for item {i}. Error: {e_general}. Skipping item.")
            continue


        # 1. BLEU Score
        if ref_tokens and pred_tokens:
            try:
                bleu = sentence_bleu([ref_tokens], pred_tokens, smoothing_function=CHENCHERRY.method4)
            except ZeroDivisionError: bleu = 0.0
        else: bleu = 0.0
        bleu_scores.append(bleu)

        # 2. METEOR Score

        if ref_tokens and pred_tokens:
            try:

                meteor = meteor_score([ref_tokens], pred_tokens)
            except Exception as e:
                # print(f"Warning: METEOR calculation failed for item {i}. Error: {e}. Setting to 0.")
                meteor = 0.0
        else: meteor = 0.0
        meteor_scores.append(meteor)

        # 3. Story Lengths
        predicted_lengths.append(len(pred_tokens))
        reference_lengths.append(len(ref_tokens))

    if not bleu_scores:
        print(f"No valid data processed for {filepath}. Cannot compute averages.")
        return None

    avg_metrics = {
        "bleu": np.mean(bleu_scores) if bleu_scores else 0,
        "meteor": np.mean(meteor_scores) if meteor_scores else 0,
        "avg_predicted_length": np.mean(predicted_lengths) if predicted_lengths else 0,
        "avg_reference_length": np.mean(reference_lengths) if reference_lengths else 0,
    }
    print(f"Finished processing {filepath}. Averages: {avg_metrics}")
    return avg_metrics

# Plotting Functions
def plot_metric_comparison(labels, scores_dict, title, ylabel, filename):
    if not labels or not scores_dict or not any(scores_dict.values()): # Check if scores_dict has any non-empty values
        print(f"No valid data to plot for {title}. Skipping plot generation for {filename}.")
        return

    model_labels = list(scores_dict.keys())
    metric_values = [scores_dict.get(label, 0) for label in model_labels] # Use get for safety

    fig, ax = plt.subplots(figsize=(max(8, len(model_labels) * 1.5), 6))
    colors = ['skyblue', 'lightcoral', 'lightgreen', 'gold', 'plum', 'lightsalmon']
    bar_colors = colors[:len(model_labels)] if len(model_labels) <= len(colors) else plt.cm.get_cmap('viridis')(np.linspace(0, 1, len(model_labels)))


    bars = ax.bar(model_labels, metric_values, color=bar_colors)
    ax.set_ylabel(ylabel)
    ax.set_title(title)
    ax.set_xticklabels(model_labels, rotation=25, ha="right")
    for bar in bars:
        yval = bar.get_height()
        plt.text(bar.get_x() + bar.get_width()/2.0, yval, f'{yval:.3f}', va='bottom', ha='center', fontsize=9)
    fig.tight_layout()
    plt.savefig(os.path.join(PLOTS_DIR, filename))
    print(f"Saved plot: {os.path.join(PLOTS_DIR, filename)}")
    plt.close(fig)

def plot_story_length_comparison(labels, pred_lengths, ref_lengths, title, ylabel, filename):
    if not labels or (not pred_lengths and not ref_lengths) or (len(pred_lengths)==0 and len(ref_lengths)==0): # more robust check
        print(f"No valid data to plot for {title} (story length). Skipping plot generation for {filename}.")
        return

    x = np.arange(len(labels))
    width = 0.35
    fig, ax = plt.subplots(figsize=(max(10, len(labels) * 2), 6))
    rects1 = ax.bar(x - width/2, pred_lengths, width, label='Avg. Predicted Length', color='skyblue')
    rects2 = ax.bar(x + width/2, ref_lengths, width, label='Avg. Reference Length', color='lightcoral')
    ax.set_ylabel(ylabel)
    ax.set_title(title)
    ax.set_xticks(x)
    ax.set_xticklabels(labels, rotation=25, ha="right")
    ax.legend()
    def autolabel(rects):
        for rect in rects:
            height = rect.get_height()
            ax.annotate(f'{height:.1f}',
                        xy=(rect.get_x() + rect.get_width() / 2, height),
                        xytext=(0, 3), textcoords="offset points",
                        ha='center', va='bottom', fontsize=9)
    autolabel(rects1)
    autolabel(rects2)
    fig.tight_layout()
    plt.savefig(os.path.join(PLOTS_DIR, filename))
    print(f"Saved plot: {os.path.join(PLOTS_DIR, filename)}")
    plt.close(fig)

# Main execution
if __name__ == "__main__":
    base_path = "/content/drive/MyDrive/Project VIST with LLM/results/"

    files_to_process = [
        {"path": os.path.join(base_path, "results_gemini20_eng.json"), "label": "Gemini-Eng", "lang": "english"},
        {"path": os.path.join(base_path, "results_gemini20_spa.json"), "label": "Gemini-Spa", "lang": "spanish"},
        {"path": os.path.join(base_path, "results_gemma3_eng.json"), "label": "Gemma-Eng", "lang": "english"},
        {"path": os.path.join(base_path, "results_gemma3_spa.json"), "label": "Gemma-Spa", "lang": "spanish"},
    ]

    all_model_results = {}

    for file_info in files_to_process:
        print(f"\n--- Processing: {file_info['label']} ({file_info['path']}) ---")
        avg_scores = calculate_metrics_for_file(file_info["path"], language_code=file_info["lang"]) # Pass language
        if avg_scores:
            all_model_results[file_info["label"]] = avg_scores
        else:
            print(f"Failed to process or no valid data in {file_info['path']}. Adding placeholder.")
            all_model_results[file_info["label"]] = {"bleu": 0, "meteor": 0, "avg_predicted_length": 0, "avg_reference_length": 0}

    if not all_model_results or all(v is None for v in all_model_results.values()):
        print("\nNo results were successfully processed. Skipping plotting.")
    else:
        print("\n--- Generating Plots ---")
        model_labels_for_plot = [label for label, res in all_model_results.items() if res is not None]

        if not model_labels_for_plot:
            print("No valid model results available for plotting.")
        else:
            # Plot BLEU
            bleu_data = {label: all_model_results[label].get("bleu", 0) for label in model_labels_for_plot}
            plot_metric_comparison(model_labels_for_plot, bleu_data, "Average BLEU Score Comparison", "BLEU Score (Higher is Better)", "bleu_scores.png")

            # Plot METEOR
            meteor_data = {label: all_model_results[label].get("meteor", 0) for label in model_labels_for_plot}
            plot_metric_comparison(model_labels_for_plot, meteor_data, "Average METEOR Score Comparison", "METEOR Score (Higher is Better)", "meteor_scores.png")

            # Plot Story Lengths
            pred_lengths = [all_model_results[label].get("avg_predicted_length", 0) for label in model_labels_for_plot]
            ref_lengths = [all_model_results[label].get("avg_reference_length", 0) for label in model_labels_for_plot]
            plot_story_length_comparison(model_labels_for_plot, pred_lengths, ref_lengths, "Average Story Length Comparison (Word Count)", "Average Word Count", "story_lengths.png")

    print("\n--- Script Finished ---")

NLTK resource 'punkt' already available.
NLTK resource 'wordnet' downloaded successfully.
NLTK resource 'omw-1.4' downloaded successfully.
NLTK resource 'averaged_perceptron_tagger' already available.

--- Processing: Gemini-Eng (/content/drive/MyDrive/Project VIST with LLM/results/results_gemini20_eng.json) ---
Processing /content/drive/MyDrive/Project VIST with LLM/results/results_gemini20_eng.json (473 items) for language: english...
Finished processing /content/drive/MyDrive/Project VIST with LLM/results/results_gemini20_eng.json. Averages: {'bleu': np.float64(0.01313281813170976), 'meteor': np.float64(0.14884754694322977), 'avg_predicted_length': np.float64(139.52642706131078), 'avg_reference_length': np.float64(207.1585623678647)}

--- Processing: Gemini-Spa (/content/drive/MyDrive/Project VIST with LLM/results/results_gemini20_spa.json) ---
Processing /content/drive/MyDrive/Project VIST with LLM/results/results_gemini20_spa.json (127 items) for language: spanish...
Finished proc

<ipython-input-42-5c570cb2f1ab>:173: UserWarning: set_ticklabels() should only be used with a fixed number of ticks, i.e. after set_ticks() or using a FixedLocator.
  ax.set_xticklabels(model_labels, rotation=25, ha="right")
<ipython-input-42-5c570cb2f1ab>:173: UserWarning: set_ticklabels() should only be used with a fixed number of ticks, i.e. after set_ticks() or using a FixedLocator.
  ax.set_xticklabels(model_labels, rotation=25, ha="right")


Saved plot: comparison_plots/meteor_scores.png
Saved plot: comparison_plots/story_lengths.png

--- Script Finished ---


In [ ]:
from google.colab import drive
import json
import os

# Mount Google Drive
drive.mount('/content/drive')

Mounted at /content/drive


In [ ]:
nltk.download('punkt')
nltk.download('punkt_tab')

[nltk_data] Downloading package punkt to /root/nltk_data...
[nltk_data]   Package punkt is already up-to-date!
[nltk_data] Downloading package punkt_tab to /root/nltk_data...
[nltk_data]   Unzipping tokenizers/punkt_tab.zip.


True

In [ ]:
!pip install bert-score

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 61.1/61.1 kB 3.5 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 363.4/363.4 MB 4.9 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 13.8/13.8 MB 66.7 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 24.6/24.6 MB 36.7 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 883.7/883.7 kB 54.3 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 664.8/664.8 MB 2.2 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 211.5/211.5 MB 5.9 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 56.3/56.3 MB 15.1 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 127.9/127.9 MB 7.6 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 207.5/207.5 MB 5.6 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 21.1/21.1 MB 84.3 MB/s eta 0:00:00
  Attempting uninstall: nvidia-nvjitlink-cu12
    Found existing installation: nvidia-nvjitlink-cu12 12.5.82
    Uninstalling

In [ ]:
import json
import numpy as np
from bert_score import score as bert_scorer_fn # Renamed to avoid conflict
import os
import torch # BERTScore uses PyTorch

# Global Settings & Initializations
PLOTS_DIR = "/content/drive/MyDrive/Project VIST with LLM/results/bertscore_results" # We can save individual scores if needed
os.makedirs(PLOTS_DIR, exist_ok=True)

# Check for GPU availability for BERTScore
DEVICE = "cuda" if torch.cuda.is_available() else "cpu"
print(f"BERTScore will use device: {DEVICE}")

# BERTScore Calculation Function
def calculate_bertscore_for_file(filepath, language_code='en'): # Default to 'en' for lang parameter
    """
    Loads a JSON file, calculates BERTScore (P, R, F1) for each item,
    and returns average P, R, F1.
    'language_code' is for the 'lang' parameter of BERTScore.
    """
    precision_scores = []
    recall_scores = []
    f1_scores = []

    try:
        with open(filepath, 'r', encoding='utf-8') as f:
            data = json.load(f)
    except FileNotFoundError:
        print(f"Error: File not found at {filepath}")
        return None
    except json.JSONDecodeError:
        print(f"Error: Could not decode JSON from {filepath}")
        return None

    if not isinstance(data, list):
        print(f"Error: Expected a list of items in {filepath}, but got {type(data)}")
        return None

    print(f"Calculating BERTScore for {filepath} ({len(data)} items), lang='{language_code}'...")

    # Prepare all candidates and references for batch processing if possible
    all_candidates = []
    all_references = []
    valid_item_indices = [] # To map results back if some items are skipped

    for i, item in enumerate(data):
        if not isinstance(item, dict):
            print(f"Warning: Item {i} in {filepath} is not a dictionary. Skipping.")
            continue

        reference_segments = item.get("texts")
        predicted_segments = item.get("predicted_texts")

        if reference_segments is None or predicted_segments is None:
            print(f"Warning: Missing 'texts' or 'predicted_texts' in item {i} of {filepath}. Skipping.")
            continue
        if not isinstance(reference_segments, list) or not isinstance(predicted_segments, list):
            print(f"Warning: 'texts' or 'predicted_texts' is not a list in item {i} of {filepath}. Skipping.")
            continue

        reference_segments = [str(s) for s in reference_segments]
        predicted_segments = [str(s) for s in predicted_segments]

        full_reference_story = " ".join(reference_segments)
        full_predicted_story = " ".join(predicted_segments)

        if not full_reference_story.strip() or not full_predicted_story.strip():

            all_candidates.append("") # Add empty string to maintain batch alignment if other is not empty
            all_references.append("")
        else:
            all_candidates.append(full_predicted_story)
            all_references.append(full_reference_story)

        valid_item_indices.append(i)


    if not all_candidates: # If all items were skipped or file was empty
        print(f"No valid candidate/reference pairs to process for {filepath}.")
        return None

    # Calculate BERTScore in batches
    try:
        P, R, F1 = bert_scorer_fn(
            all_candidates,
            all_references,
            lang=language_code, # e.g., 'en', 'es'
            model_type='bert-base-multilingual-cased', # Good general multilingual model
            device=DEVICE,
            verbose=False, # Set to True for more progress details
            batch_size=16 # Adjust based on GPU memory
        )
        precision_scores.extend(P.tolist())
        recall_scores.extend(R.tolist())
        f1_scores.extend(F1.tolist())

    except Exception as e:
        print(f"Error during BERTScore calculation for {filepath}: {e}")
        # Fallback to item-by-item if batch fails (e.g. OOM), though less efficient
        print("Attempting item-by-item BERTScore calculation as fallback...")
        precision_scores, recall_scores, f1_scores = [], [], [] # Reset lists
        for cand, ref in zip(all_candidates, all_references):
            if not cand.strip() or not ref.strip():
                precision_scores.append(0.0)
                recall_scores.append(0.0)
                f1_scores.append(0.0)
                continue
            try:
                p_single, r_single, f1_single = bert_scorer_fn(
                    [cand], [ref], lang=language_code, model_type='bert-base-multilingual-cased', device=DEVICE, verbose=False
                )
                precision_scores.append(p_single.item())
                recall_scores.append(r_single.item())
                f1_scores.append(f1_single.item())
            except Exception as e_single:
                print(f"  Error on single item: {e_single}. Setting scores to 0 for this item.")
                precision_scores.append(0.0)
                recall_scores.append(0.0)
                f1_scores.append(0.0)


    if not f1_scores:
        print(f"BERTScore calculation resulted in no scores for {filepath}.")
        return None

    avg_metrics = {
        "bertscore_precision_avg": np.mean(precision_scores) if precision_scores else 0,
        "bertscore_recall_avg": np.mean(recall_scores) if recall_scores else 0,
        "bertscore_f1_avg": np.mean(f1_scores) if f1_scores else 0,
    }
    print(f"Finished BERTScore for {filepath}. Averages: {avg_metrics}")
    return avg_metrics

# Main Execution
if __name__ == "__main__":


    base_path = "/content/drive/MyDrive/Project VIST with LLM/results/"

    files_to_process = [
        {"path": os.path.join(base_path, "results_gemini20_eng.json"), "label": "Gemini-Eng", "lang_code": "en"},
        {"path": os.path.join(base_path, "results_gemini20_spa.json"), "label": "Gemini-Spa", "lang_code": "es"},
        {"path": os.path.join(base_path, "results_gemma3_eng.json"), "label": "Gemma-Eng", "lang_code": "en"},
        {"path": os.path.join(base_path, "results_gemma3_spa.json"), "label": "Gemma-Spa", "lang_code": "es"},
    ]

    all_bertscore_results = {} # Store results as { 'Model-Lang Label': {bertscore_averages} }

    for file_info in files_to_process:
        print(f"\n--- Calculating BERTScore for: {file_info['label']} ({file_info['path']}) ---")
        # Pass the language code for BERTScore's 'lang' parameter
        avg_scores = calculate_bertscore_for_file(file_info["path"], language_code=file_info["lang_code"])
        if avg_scores:
            all_bertscore_results[file_info["label"]] = avg_scores
        else:
            print(f"Failed to calculate BERTScore for {file_info['path']}. Adding placeholder.")
            all_bertscore_results[file_info["label"]] = {
                "bertscore_precision_avg": 0,
                "bertscore_recall_avg": 0,
                "bertscore_f1_avg": 0
            }

    print("\n\n--- Aggregated BERTScore Results ---")
    if not all_bertscore_results or all(v is None for v in all_bertscore_results.values()):
        print("No BERTScore results were successfully calculated.")
    else:
        for label, scores in all_bertscore_results.items():
            if scores: # Check if scores dict is not None
                print(f"\nResults for: {label}")
                print(f"  Average BERTScore Precision: {scores.get('bertscore_precision_avg', 0):.4f}")
                print(f"  Average BERTScore Recall:    {scores.get('bertscore_recall_avg', 0):.4f}")
                print(f"  Average BERTScore F1:        {scores.get('bertscore_f1_avg', 0):.4f}")
            else:
                print(f"\nNo scores calculated for: {label}")


    # Plotting (Example for F1 scores)

    print("\n--- Generating Example Plot for BERTScore F1 (if data available) ---")

    model_labels_for_plot = [label for label, res in all_bertscore_results.items() if res is not None]
    if model_labels_for_plot:
        f1_data_for_plot = {label: all_bertscore_results[label].get("bertscore_f1_avg", 0) for label in model_labels_for_plot}

        if any(f1_data_for_plot.values()): # Check if there's any non-zero F1 score to plot
            fig, ax = plt.subplots(figsize=(max(8, len(model_labels_for_plot) * 1.5), 6))
            colors = ['skyblue', 'lightcoral', 'lightgreen', 'gold', 'plum']
            bar_colors = colors[:len(model_labels_for_plot)] if len(model_labels_for_plot) <= len(colors) else plt.cm.get_cmap('viridis')(np.linspace(0,1,len(model_labels_for_plot)))

            bars = ax.bar(model_labels_for_plot, list(f1_data_for_plot.values()), color=bar_colors)
            ax.set_ylabel("Average BERTScore F1 (Higher is Better)")
            ax.set_title("BERTScore F1 Comparison")
            ax.set_xticklabels(model_labels_for_plot, rotation=25, ha="right")
            for bar in bars:
                yval = bar.get_height()
                plt.text(bar.get_x() + bar.get_width()/2.0, yval, f'{yval:.3f}', va='bottom', ha='center', fontsize=9)
            fig.tight_layout()
            plot_filename = os.path.join(PLOTS_DIR, "bertscore_f1_comparison.png")
            plt.savefig(plot_filename)
            print(f"Saved example BERTScore F1 plot: {plot_filename}")
            plt.close(fig)
        else:
            print("No valid BERTScore F1 data to plot (all scores might be zero or processing failed).")
    else:
        print("No model labels with results available for plotting BERTScore.")

    print("\n--- BERTScore Calculation Script Finished ---")

BERTScore will use device: cuda

--- Calculating BERTScore for: Gemini-Eng (/content/drive/MyDrive/Project VIST with LLM/results/results_gemini20_eng.json) ---
Calculating BERTScore for /content/drive/MyDrive/Project VIST with LLM/results/results_gemini20_eng.json (473 items), lang='en'...


tokenizer_config.json:   0%|          | 0.00/49.0 [00:00<?, ?B/s]

config.json:   0%|          | 0.00/625 [00:00<?, ?B/s]

vocab.txt:   0%|          | 0.00/996k [00:00<?, ?B/s]

tokenizer.json:   0%|          | 0.00/1.96M [00:00<?, ?B/s]

model.safetensors:   0%|          | 0.00/714M [00:00<?, ?B/s]

Finished BERTScore for /content/drive/MyDrive/Project VIST with LLM/results/results_gemini20_eng.json. Averages: {'bertscore_precision_avg': np.float64(0.6458769785929432), 'bertscore_recall_avg': np.float64(0.6409961669439997), 'bertscore_f1_avg': np.float64(0.6425623634148854)}

--- Calculating BERTScore for: Gemini-Spa (/content/drive/MyDrive/Project VIST with LLM/results/results_gemini20_spa.json) ---
Calculating BERTScore for /content/drive/MyDrive/Project VIST with LLM/results/results_gemini20_spa.json (127 items), lang='es'...
Finished BERTScore for /content/drive/MyDrive/Project VIST with LLM/results/results_gemini20_spa.json. Averages: {'bertscore_precision_avg': np.float64(0.6519881364867444), 'bertscore_recall_avg': np.float64(0.6608755569758378), 'bertscore_f1_avg': np.float64(0.655827118655828)}

--- Calculating BERTScore for: Gemma-Eng (/content/drive/MyDrive/Project VIST with LLM/results/results_gemma3_eng.json) ---
Calculating BERTScore for /content/drive/MyDrive/Projec

<ipython-input-9-ed9e965ddb15>:206: UserWarning: set_ticklabels() should only be used with a fixed number of ticks, i.e. after set_ticks() or using a FixedLocator.
  ax.set_xticklabels(model_labels_for_plot, rotation=25, ha="right")


In [ ]:
!pip install textstat

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 175.3/175.3 kB 10.2 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 939.4/939.4 kB 37.4 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 2.1/2.1 MB 30.2 MB/s eta 0:00:00


In [ ]:
import json
import nltk
from nltk.tokenize import word_tokenize, sent_tokenize
import numpy as np
import matplotlib.pyplot as plt
import os
import textstat # For syllable counting

# NLTK Resource Downloads
def download_nltk_punkt():
    try:
        nltk.data.find('tokenizers/punkt')
        print("NLTK resource 'punkt' already available.")
    except LookupError:
        print("Downloading NLTK resource 'punkt'...")
        try:
            nltk.download('punkt', quiet=True)
            print("NLTK resource 'punkt' downloaded successfully.")
        except Exception as e:
            print(f"Error downloading NLTK resource 'punkt': {e}")

download_nltk_punkt()

# Global Settings
PLOTS_DIR = "/content/drive/MyDrive/Project VIST with LLM/results/fkgl_readability_plots_v2" # New directory for these plots
os.makedirs(PLOTS_DIR, exist_ok=True)

# FKGL Formula constants
A_FKGL = 0.39
B_FKGL = 11.8
C_FKGL = -15.59

# FKGL Calculation Function
def calculate_fkgl(text_content):
    if not text_content or not text_content.strip(): return None
    try:
        sentences = sent_tokenize(text_content)
        words = word_tokenize(text_content.lower())
    except Exception: return None
    num_sentences = len(sentences)
    actual_words = [word for word in words if word.isalnum()]
    num_words = len(actual_words)
    if num_sentences == 0 or num_words == 0: return None
    num_syllables = 0
    for word in actual_words:
        try: num_syllables += textstat.syllable_count(word)
        except Exception: pass
    words_per_sentence = num_words / num_sentences
    syllables_per_word = num_syllables / num_words if num_words > 0 else 0
    fkgl_score = (A_FKGL * words_per_sentence) + (B_FKGL * syllables_per_word) + C_FKGL
    return fkgl_score

# File Processing Function (Modified to return baseline and predicted FKGL)
def process_files_for_fkgl_v2(filepath):
    """
    Loads a JSON file and calculates average FKGL for 'predicted_texts' AND 'texts' (baseline).
    Returns a dict with 'avg_predicted_fkgl' and 'avg_baseline_fkgl'.
    """
    predicted_fkgl_scores = []
    baseline_fkgl_scores = []

    try:
        with open(filepath, 'r', encoding='utf-8') as f:
            data = json.load(f)
    except FileNotFoundError:
        print(f"Error: File not found at {filepath}")
        return None
    except json.JSONDecodeError:
        print(f"Error: Could not decode JSON from {filepath}")
        return None
    if not isinstance(data, list):
        print(f"Error: Expected a list of items in {filepath}, but got {type(data)}")
        return None

    print(f"Calculating FKGL for {filepath} ({len(data)} items)...")

    for i, item in enumerate(data):
        if not isinstance(item, dict): continue

        # Process Predicted Texts
        predicted_segments = item.get("predicted_texts")
        if predicted_segments and isinstance(predicted_segments, list):
            full_predicted_story = " ".join([str(s) for s in predicted_segments])
            if full_predicted_story.strip():
                fkgl_pred = calculate_fkgl(full_predicted_story)
                if fkgl_pred is not None:
                    predicted_fkgl_scores.append(fkgl_pred)

        # Process Baseline Texts
        baseline_segments = item.get("texts") # Assuming 'texts' is the key for baseline
        if baseline_segments and isinstance(baseline_segments, list):
            full_baseline_story = " ".join([str(s) for s in baseline_segments])
            if full_baseline_story.strip():
                fkgl_base = calculate_fkgl(full_baseline_story)
                if fkgl_base is not None:
                    baseline_fkgl_scores.append(fkgl_base)

    results = {}
    if predicted_fkgl_scores:
        results["avg_predicted_fkgl"] = np.mean(predicted_fkgl_scores)
    else:
        results["avg_predicted_fkgl"] = np.nan # Use NaN if no scores

    if baseline_fkgl_scores:
        results["avg_baseline_fkgl"] = np.mean(baseline_fkgl_scores)
    else:
        results["avg_baseline_fkgl"] = np.nan

    if not predicted_fkgl_scores and not baseline_fkgl_scores:
        print(f"No FKGL scores could be calculated for {filepath}.")
        return None # Return None if no scores were calculated at all

    print(f"Finished FKGL for {filepath}. Predicted Avg: {results.get('avg_predicted_fkgl', 'N/A'):.2f}, Baseline Avg: {results.get('avg_baseline_fkgl', 'N/A'):.2f}")
    return results


# Plotting Function
def plot_fkgl_language_group(language_name, model_data, title, ylabel, filename):
    """
    Creates a grouped bar chart for FKGL scores for a specific language.
    model_data: A dictionary like {'Gemini': {'predicted': 7.5, 'baseline': 7.0}, 'Gemma': {...}}
    """
    model_names = list(model_data.keys())
    if not model_names:
        print(f"No model data provided for {language_name} plot. Skipping.")
        return

    predicted_scores = [model_data[model].get('predicted', np.nan) for model in model_names]
    baseline_scores = [model_data[model].get('baseline', np.nan) for model in model_names]

    x = np.arange(len(model_names))  # the label locations for models
    width = 0.35  # the width of the bars

    fig, ax = plt.subplots(figsize=(max(8, len(model_names) * 2.5), 6))
    rects1 = ax.bar(x - width/2, predicted_scores, width, label='Predicted FKGL', color='skyblue')
    rects2 = ax.bar(x + width/2, baseline_scores, width, label='Baseline FKGL', color='lightcoral')

    ax.set_ylabel(ylabel)
    ax.set_title(f'{title} - {language_name}')
    ax.set_xticks(x)
    ax.set_xticklabels(model_names)
    ax.legend()

    def autolabel(rects):
        for rect in rects:
            height = rect.get_height()
            if not np.isnan(height): # Only label if not NaN
                ax.annotate(f'{height:.2f}',
                            xy=(rect.get_x() + rect.get_width() / 2, height),
                            xytext=(0, 3),  # 3 points vertical offset
                            textcoords="offset points",
                            ha='center', va='bottom', fontsize=9)
    autolabel(rects1)
    autolabel(rects2)

    fig.tight_layout()
    plt.savefig(os.path.join(PLOTS_DIR, filename))
    print(f"Saved FKGL plot for {language_name}: {os.path.join(PLOTS_DIR, filename)}")
    plt.close(fig)


# Main Execution
if __name__ == "__main__":
    base_path = "/content/drive/MyDrive/Project VIST with LLM/results/"

    files_to_process = [
        {"path": os.path.join(base_path, "results_gemini20_eng.json"), "model": "Gemini", "lang": "English"},
        {"path": os.path.join(base_path, "results_gemini20_spa.json"), "model": "Gemini", "lang": "Spanish"},
        {"path": os.path.join(base_path, "results_gemma3_eng.json"), "model": "Gemma", "lang": "English"},
        {"path": os.path.join(base_path, "results_gemma3_spa.json"), "model": "Gemma", "lang": "Spanish"},
    ]

    # Restructure data for plotting: { 'English': {'Gemini': {'predicted': X, 'baseline': Y}, ...}, 'Spanish': ... }
    all_language_fkgl_results = {"English": {}, "Spanish": {}}

    for file_info in files_to_process:
        print(f"\n--- Calculating FKGL for: {file_info['model']} ({file_info['lang']}) ---")
        fkgl_data = process_files_for_fkgl_v2(file_info["path"])

        model_name = file_info["model"]
        language = file_info["lang"]

        if fkgl_data:
            all_language_fkgl_results[language][model_name] = {
                "predicted": fkgl_data.get("avg_predicted_fkgl", np.nan),
                "baseline": fkgl_data.get("avg_baseline_fkgl", np.nan)
            }
        else:
            print(f"No FKGL data returned for {model_name} ({language}). Storing NaNs.")
            all_language_fkgl_results[language][model_name] = {
                "predicted": np.nan,
                "baseline": np.nan
            }

    print("\n\n--- Aggregated Flesch-Kincaid Grade Level (FKGL) Results ---")
    for lang, models_data in all_language_fkgl_results.items():
        print(f"\nLanguage: {lang}")
        if not models_data:
            print("  No data processed for this language.")
            continue
        for model, scores in models_data.items():
            pred_score = scores.get('predicted', np.nan)
            base_score = scores.get('baseline', np.nan)
            pred_str = f"{pred_score:.2f}" if not np.isnan(pred_score) else "N/A"
            base_str = f"{base_score:.2f}" if not np.isnan(base_score) else "N/A"
            print(f"  Model: {model}")
            print(f"    Average Predicted FKGL: {pred_str}")
            print(f"    Average Baseline FKGL:  {base_str}")

    # Plotting
    plot_title_base = "FKGL Comparison (Lower is Easier)"
    plot_ylabel = "FKGL Score (Reading Age approx.)"

    if all_language_fkgl_results["English"]:
        plot_fkgl_language_group(
            language_name="English",
            model_data=all_language_fkgl_results["English"],
            title=plot_title_base,
            ylabel=plot_ylabel,
            filename="fkgl_scores_english.png"
        )
    else:
        print("No data to plot for English FKGL.")

    if all_language_fkgl_results["Spanish"]:
        plot_fkgl_language_group(
            language_name="Spanish",
            model_data=all_language_fkgl_results["Spanish"],
            title=plot_title_base,
            ylabel=plot_ylabel,
            filename="fkgl_scores_spanish.png"
        )
    else:
        print("No data to plot for Spanish FKGL.")


    print("\n--- FKGL Calculation Script Finished ---")

NLTK resource 'punkt' already available.

--- Calculating FKGL for: Gemini (English) ---
Calculating FKGL for /content/drive/MyDrive/Project VIST with LLM/results/results_gemini20_eng.json (473 items)...
Finished FKGL for /content/drive/MyDrive/Project VIST with LLM/results/results_gemini20_eng.json. Predicted Avg: 6.81, Baseline Avg: 3.93

--- Calculating FKGL for: Gemini (Spanish) ---
Calculating FKGL for /content/drive/MyDrive/Project VIST with LLM/results/results_gemini20_spa.json (127 items)...
Finished FKGL for /content/drive/MyDrive/Project VIST with LLM/results/results_gemini20_spa.json. Predicted Avg: 10.81, Baseline Avg: 7.11

--- Calculating FKGL for: Gemma (English) ---
Calculating FKGL for /content/drive/MyDrive/Project VIST with LLM/results/results_gemma3_eng.json (455 items)...
Finished FKGL for /content/drive/MyDrive/Project VIST with LLM/results/results_gemma3_eng.json. Predicted Avg: 4.90, Baseline Avg: 3.92

--- Calculating FKGL for: Gemma (Spanish) ---
Calculating F

In [ ]:
import json
import nltk
from nltk.tokenize import word_tokenize, sent_tokenize
from nltk.util import ngrams
from collections import Counter
import numpy as np
import matplotlib.pyplot as plt
import os

#  NLTK Resource Downloads
def download_nltk_punkt():
    try:
        nltk.data.find('tokenizers/punkt')
        print("NLTK resource 'punkt' already available.")
    except LookupError:
        print("Downloading NLTK resource 'punkt'...")
        try: nltk.download('punkt', quiet=True)
        except Exception as e: print(f"Error downloading 'punkt': {e}")
download_nltk_punkt()

# Global Settings
PLOTS_DIR = "/content/drive/MyDrive/Project VIST with LLM/results/repetition_plots"
os.makedirs(PLOTS_DIR, exist_ok=True)
TRIGRAM_N = 3 # We are focusing on trigrams

# Helper Functions for Trigrams
def get_trigrams_from_sentence(sentence_text, n=TRIGRAM_N):
    """Returns a list of trigram strings from a tokenized sentence."""
    if not sentence_text or not sentence_text.strip():
        return []
    try:
        tokens = word_tokenize(sentence_text.lower())
    except Exception: # Handle tokenization errors on odd inputs
        return []
    if len(tokens) < n:
        return []
    return [" ".join(gram) for gram in ngrams(tokens, n)]

def get_distinct_trigrams_set(sentence_text, n=TRIGRAM_N):
    """Returns a set of distinct trigram strings."""
    return set(get_trigrams_from_sentence(sentence_text, n))

def T_distinct_count(list_of_sentence_texts, n=TRIGRAM_N):
    """Calculates T(X) - number of distinct n-grams in a collection of sentences."""
    all_distinct_trigrams = set()
    for text in list_of_sentence_texts:
        all_distinct_trigrams.update(get_distinct_trigrams_set(text, n))
    return len(all_distinct_trigrams)

def T_all_count(list_of_sentence_texts, n=TRIGRAM_N):
    """Calculates T_all(X) - total number of n-grams in a collection of sentences."""
    total_count = 0
    for text in list_of_sentence_texts:
        total_count += len(get_trigrams_from_sentence(text, n))
    return total_count

# Repetition Metric Calculation Functions

def calculate_r_e_agg(all_stories_sentences):
    """
    Calculates aggregate inter-story repetition r_e^{agg}.
    all_stories_sentences: A flat list of all sentence strings from all stories.
    """
    if not all_stories_sentences:
        return np.nan # Or 0, depending on how you want to treat empty input

    distinct_count = T_distinct_count(all_stories_sentences)
    total_count = T_all_count(all_stories_sentences)

    if total_count == 0:
        return 0.0 # No trigrams means no repetition (or perfect diversity in a way)

    r_e_agg = 1.0 - (distinct_count / total_count)
    return r_e_agg

def calculate_story_r_a_values(story_sentences):
    """
    Calculates r_a^i for each sentence i in a single story.
    story_sentences: A list of sentence strings for one story.
    Returns a list of r_a^i values, one for each sentence. r_a^1 will be 0.
    """
    num_sentences_in_story = len(story_sentences)
    if num_sentences_in_story == 0:
        return []

    r_a_i_values = [0.0] * num_sentences_in_story # Initialize with 0s

    # Pre-calculate distinct trigrams for all sentences in this story
    story_sentence_distinct_trigrams = [get_distinct_trigrams_set(s) for s in story_sentences]

    for i in range(1, num_sentences_in_story): # Start from the second sentence (index 1)
        s_i_distinct_trigrams = story_sentence_distinct_trigrams[i]
        T_s_i = len(s_i_distinct_trigrams)

        if T_s_i == 0 or (i - 1 + 1) == 1: # (i-1) in formula, so i starts at 1 for sentence index in paper, 0 here.
                                       # (i-1) in denominator means i must be > 1 (sentence index)
                                       # Number of previous sentences is 'i'
            r_a_i_values[i] = 0.0 # Or handle as per paper if T(s^i) = 0 is an issue
            continue

        sum_T_s_i_intersect_s_k = 0
        for k in range(i): # Iterate through all previous sentences (0 to i-1)
            s_k_distinct_trigrams = story_sentence_distinct_trigrams[k]
            common_trigrams = s_i_distinct_trigrams.intersection(s_k_distinct_trigrams)
            sum_T_s_i_intersect_s_k += len(common_trigrams)

        # Denominator: (i-1) * T(s^i) in paper. Here, number of previous sentences is 'i'.
        # So, (number of preceding sentences) * T(s^i)
        denominator = i * T_s_i # 'i' here is the count of preceding sentences (0 to i-1)
        if denominator == 0:
            r_a_i_values[i] = 0.0 # Or some other value indicating high repetition if sum_T is high
        else:
            r_a_i_values[i] = sum_T_s_i_intersect_s_k / denominator

    return r_a_i_values


def calculate_dataset_r_a_agg(all_stories_parsed):
    """
    Calculates the overall r_a^{agg} for the dataset.
    all_stories_parsed: list of lists, where each inner list contains sentence strings for a story.
    This implementation calculates r_a^{agg} for each story and then averages them.
    """
    story_level_r_a_agg_scores = []
    for story_sentences in all_stories_parsed:
        if not story_sentences:
            continue
        r_a_i_values_for_story = calculate_story_r_a_values(story_sentences)
        if r_a_i_values_for_story: # Ensure not empty
            # The paper's r_a^{agg} = (1/m) * sum(r_a^i).
            # Here, m is the number of sentences in *this* story.
            # We exclude r_a^0 (which is always 0) from the average if it makes sense.
            # The formula r_a^i is for i=1 to m. Our r_a_i_values list is 0-indexed.
            # So r_a_i_values[0] corresponds to r_a^1 (which should be 0).
            # Let's average r_a^i for i >= 1 (index >=0 in list, but really for sentences 2 onwards)

            # If r_a^1 is defined as 0 and included in the average as per sum i=1 to m:
            story_agg = np.mean(r_a_i_values_for_story)
            story_level_r_a_agg_scores.append(story_agg)

    if not story_level_r_a_agg_scores:
        return np.nan
    return np.mean(story_level_r_a_agg_scores)


# File Processing Function
def process_file_for_repetition(filepath):
    """
    Loads a JSON file, calculates repetition metrics for 'predicted_texts' and 'texts' (baseline).
    """
    all_predicted_story_sentences_flat = []
    all_baseline_story_sentences_flat = []

    parsed_predicted_stories = [] # List of [sentence_list_for_story1, sentence_list_for_story2, ...]
    parsed_baseline_stories = []

    try:
        with open(filepath, 'r', encoding='utf-8') as f:
            data = json.load(f)
    except Exception as e:
        print(f"Error loading/parsing {filepath}: {e}")
        return None
    if not isinstance(data, list):
        print(f"Error: Expected a list of items in {filepath}")
        return None

    print(f"Processing repetition for {filepath} ({len(data)} items)...")

    for i, item in enumerate(data):
        if not isinstance(item, dict): continue

        # Process Predicted Texts
        predicted_segments = item.get("predicted_texts")
        if predicted_segments and isinstance(predicted_segments, list):
            story_sentences_pred = []
            for seg_text in predicted_segments:
                seg_text_str = str(seg_text)
                if seg_text_str.strip():
                    # The paper implies s^ji is a sentence.
                    sents_in_seg = sent_tokenize(seg_text_str)
                    story_sentences_pred.extend(sents_in_seg)
            if story_sentences_pred:
                all_predicted_story_sentences_flat.extend(story_sentences_pred)
                parsed_predicted_stories.append(story_sentences_pred)

        # Process Baseline Texts
        baseline_segments = item.get("texts")
        if baseline_segments and isinstance(baseline_segments, list):
            story_sentences_base = []
            for seg_text in baseline_segments:
                seg_text_str = str(seg_text)
                if seg_text_str.strip():
                    sents_in_seg = sent_tokenize(seg_text_str)
                    story_sentences_base.extend(sents_in_seg)
            if story_sentences_base:
                all_baseline_story_sentences_flat.extend(story_sentences_base)
                parsed_baseline_stories.append(story_sentences_base)

    results = {}
    # Inter-story repetition (r_e^{agg})
    results["predicted_r_e_agg"] = calculate_r_e_agg(all_predicted_story_sentences_flat)
    results["baseline_r_e_agg"] = calculate_r_e_agg(all_baseline_story_sentences_flat)

    # Intra-story repetition (r_a^{agg})
    results["predicted_r_a_agg"] = calculate_dataset_r_a_agg(parsed_predicted_stories)
    results["baseline_r_a_agg"] = calculate_dataset_r_a_agg(parsed_baseline_stories)

    print(f"Finished repetition for {filepath}. Predicted r_e_agg: {results['predicted_r_e_agg']:.4f}, r_a_agg: {results['predicted_r_a_agg']:.4f}. "
          f"Baseline r_e_agg: {results['baseline_r_e_agg']:.4f}, r_a_agg: {results['baseline_r_a_agg']:.4f}")
    return results

# Plotting Function
def plot_repetition_metrics_language_group(language_name, model_data, title, filename):
    """
    model_data: {'Gemini': {'predicted_r_e': X, 'baseline_r_e': Y, 'predicted_r_a': Z, 'baseline_r_a': W}, ...}
    """
    model_names = list(model_data.keys())
    if not model_names:
        print(f"No model data for {language_name} repetition plot. Skipping.")
        return

    n_models = len(model_names)
    bar_width = 0.20  # Width of each individual bar
    index = np.arange(n_models) # Model indices

    fig, ax = plt.subplots(figsize=(max(10, n_models * 4), 7))

    # Scores for each category
    pred_r_e = [model_data[model].get('predicted_r_e_agg', np.nan) for model in model_names]
    base_r_e = [model_data[model].get('baseline_r_e_agg', np.nan) for model in model_names]
    pred_r_a = [model_data[model].get('predicted_r_a_agg', np.nan) for model in model_names]
    base_r_a = [model_data[model].get('baseline_r_a_agg', np.nan) for model in model_names]

    rects1 = ax.bar(index - 1.5*bar_width, pred_r_e, bar_width, label='Predicted Inter-Rep (r_e)', color='cornflowerblue')
    rects2 = ax.bar(index - 0.5*bar_width, base_r_e, bar_width, label='Baseline Inter-Rep (r_e)', color='lightsteelblue')
    rects3 = ax.bar(index + 0.5*bar_width, pred_r_a, bar_width, label='Predicted Intra-Rep (r_a)', color='salmon')
    rects4 = ax.bar(index + 1.5*bar_width, base_r_a, bar_width, label='Baseline Intra-Rep (r_a)', color='lightpink')

    ax.set_ylabel('Repetition Score (Higher is More Repetitive)')
    ax.set_title(f'{title} - {language_name}')
    ax.set_xticks(index)
    ax.set_xticklabels(model_names)
    ax.legend(fontsize='small', loc='upper left', bbox_to_anchor=(1,1)) # Adjust legend

    def autolabel(rects):
        for rect in rects:
            height = rect.get_height()
            if not np.isnan(height):
                ax.annotate(f'{height:.3f}',
                            xy=(rect.get_x() + rect.get_width() / 2, height),
                            xytext=(0, 3), textcoords="offset points",
                            ha='center', va='bottom', fontsize=7, rotation=45)
    autolabel(rects1); autolabel(rects2); autolabel(rects3); autolabel(rects4)

    fig.tight_layout(rect=[0, 0, 0.85, 1]) # Adjust layout to make space for legend
    plt.savefig(os.path.join(PLOTS_DIR, filename))
    print(f"Saved repetition plot for {language_name}: {os.path.join(PLOTS_DIR, filename)}")
    plt.close(fig)

# Main Execution
if __name__ == "__main__":
    base_path = "/content/drive/MyDrive/Project VIST with LLM/results/"
    files_to_process = [
        {"path": os.path.join(base_path, "results_gemini20_eng.json"), "model": "Gemini", "lang": "English"},
        {"path": os.path.join(base_path, "results_gemini20_spa.json"), "model": "Gemini", "lang": "Spanish"},
        {"path": os.path.join(base_path, "results_gemma3_eng.json"), "model": "Gemma", "lang": "English"},
        {"path": os.path.join(base_path, "results_gemma3_spa.json"), "model": "Gemma", "lang": "Spanish"},
    ]

    all_language_repetition_results = {"English": {}, "Spanish": {}}

    for file_info in files_to_process:
        print(f"\n--- Calculating Repetition for: {file_info['model']} ({file_info['lang']}) ---")
        repetition_data = process_file_for_repetition(file_info["path"])
        model_name = file_info["model"]
        language = file_info["lang"]

        if repetition_data:
            all_language_repetition_results[language][model_name] = repetition_data
        else:
            all_language_repetition_results[language][model_name] = {
                "predicted_r_e_agg": np.nan, "baseline_r_e_agg": np.nan,
                "predicted_r_a_agg": np.nan, "baseline_r_a_agg": np.nan
            }

    print("\n\n--- Aggregated Repetition Score Results ---")
    for lang, models_data in all_language_repetition_results.items():
        print(f"\nLanguage: {lang}")
        if not models_data: print("  No data processed."); continue
        for model, scores in models_data.items():
            print(f"  Model: {model}")
            for key, val in scores.items():
                val_str = f"{val:.4f}" if not np.isnan(val) else "N/A"
                print(f"    {key}: {val_str}")

    # Plotting
    plot_title_base = "Trigram Repetition Scores"
    if all_language_repetition_results["English"]:
        plot_repetition_metrics_language_group(
            "English", all_language_repetition_results["English"],
            plot_title_base, "repetition_scores_english.png"
        )
    if all_language_repetition_results["Spanish"]:
        plot_repetition_metrics_language_group(
            "Spanish", all_language_repetition_results["Spanish"],
            plot_title_base, "repetition_scores_spanish.png"
        )
    print("\n--- Repetition Calculation Script Finished ---")

NLTK resource 'punkt' already available.

--- Calculating Repetition for: Gemini (English) ---
Processing repetition for /content/drive/MyDrive/Project VIST with LLM/results/results_gemini20_eng.json (473 items)...
Finished repetition for /content/drive/MyDrive/Project VIST with LLM/results/results_gemini20_eng.json. Predicted r_e_agg: 0.1785, r_a_agg: 0.0018. Baseline r_e_agg: 0.2049, r_a_agg: 0.0159

--- Calculating Repetition for: Gemini (Spanish) ---
Processing repetition for /content/drive/MyDrive/Project VIST with LLM/results/results_gemini20_spa.json (127 items)...
Finished repetition for /content/drive/MyDrive/Project VIST with LLM/results/results_gemini20_spa.json. Predicted r_e_agg: 0.1297, r_a_agg: 0.0013. Baseline r_e_agg: 0.0973, r_a_agg: 0.0038

--- Calculating Repetition for: Gemma (English) ---
Processing repetition for /content/drive/MyDrive/Project VIST with LLM/results/results_gemma3_eng.json (455 items)...
Finished repetition for /content/drive/MyDrive/Project VIST 